In [1]:
import matplotlib.pyplot as plt
%matplotlib inline
import tensorflow as tf
import numpy as np
import pandas as pd
import io
import requests
import math
from scipy import stats

In [2]:
train=pd.read_csv('data/train.csv')
#test=pd.read_csv('data/test.csv')

In [10]:
# inputs
training_epochs = 1000
learning_rate = 0.01
hidden_layers = 199
cost_history = np.empty(shape=[1],dtype=float)

X = tf.placeholder(tf.float32,[None,feature_count])
Y = tf.placeholder(tf.float32,[None,label_count])
is_training=tf.Variable(True,dtype=tf.bool)

NameError: name 'feature_count' is not defined

In [11]:
#model

initializer = tf.contrib.layers.xavier_initializer()
h0 = tf.layers.dense(X, hidden_layers, activation=tf.nn.relu, kernel_initializer=initializer)
# h0 = tf.nn.dropout(h0, 0.95)
h1 = tf.layers.dense(h0, label_count, activation=None)

cross_entropy = tf.nn.sigmoid_cross_entropy_with_logits(labels=Y, logits=h1)
cost = tf.reduce_mean(cross_entropy)
optimizer = tf.train.AdamOptimizer(learning_rate=learning_rate).minimize(cost)

# prediction = tf.argmax(h0, 1)
# correct_prediction = tf.equal(prediction, tf.argmax(Y_one_hot, 1))
# accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

predicted = tf.nn.sigmoid(h1)
correct_pred = tf.equal(tf.round(predicted), Y)
accuracy = tf.reduce_mean(tf.cast(correct_pred, tf.float32))


Instructions for updating:
Use keras.layers.dense instead.


AttributeError: 'tuple' object has no attribute 'ndims'

In [9]:
y=train['target']
X = train.drop(['target', 'ID_code'], axis=1)
X_small=X[:100000]
y_small=y[:100000]

In [24]:
from sklearn.model_selection import train_test_split
X_train, X_valid, y_train, y_valid = train_test_split(X_small, y_small, test_size=0.2, random_state=42)

In [ ]:
# session

with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())

    for step in range(training_epochs + 1):
        sess.run(optimizer, feed_dict={X: train_X, Y: train_y})
        loss, _, acc = sess.run([cost, optimizer, accuracy], feed_dict={
                                 X: X_train, Y: y_train})
        cost_history = np.append(cost_history, acc)
        if step % 500 == 0:
            print("Step: {:5}\tLoss: {:.3f}\tAcc: {:.2%}".format(step, loss, acc))
            
    # Test model and check accuracy
    print('Test Accuracy:', sess.run([accuracy, tf.round(predicted)], feed_dict={X: X_valid, Y: y_valid}))
    print ('AUC ROC',)
    # Save test result
    #test_predict_result = sess.run(tf.cast(tf.round(predicted), tf.int32), feed_dict={X: valid_x})
    
    #evaluation = test_passenger_id.to_frame()
    #evaluation["Survived"] = test_predict_result
    #evaluation.to_csv('result.csv', index=False)

In [7]:
he_init = tf.variance_scaling_initializer()

In [12]:
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.exceptions import NotFittedError

class DNNClassifier(BaseEstimator, ClassifierMixin):
    def __init__(self, n_hidden_layers=5, n_neurons=100, optimizer_class=tf.train.AdamOptimizer,
                 learning_rate=0.01, batch_size=20, activation=tf.nn.elu, initializer=he_init,
                 batch_norm_momentum=None, dropout_rate=None, random_state=None, n_epochs=100):
        """Initialize the DNNClassifier by simply storing all the hyperparameters."""
        self.n_hidden_layers = n_hidden_layers
        self.n_neurons = n_neurons
        self.optimizer_class = optimizer_class
        self.learning_rate = learning_rate
        self.batch_size = batch_size
        self.activation = activation
        self.initializer = initializer
        self.batch_norm_momentum = batch_norm_momentum
        self.dropout_rate = dropout_rate
        self.random_state = random_state
        self._session = None
        self.n_epochs=n_epochs

    def _dnn(self, inputs):
        """Build the hidden layers, with support for batch normalization and dropout."""
        for layer in range(self.n_hidden_layers):
            if self.dropout_rate:
                inputs = tf.layers.dropout(inputs, self.dropout_rate, training=self._training)
            inputs = tf.layers.dense(inputs, self.n_neurons,
                                     kernel_initializer=self.initializer,
                                     name="hidden%d" % (layer + 1))
            if self.batch_norm_momentum:
                inputs = tf.layers.batch_normalization(inputs, momentum=self.batch_norm_momentum,
                                                       training=self._training)
            inputs = self.activation(inputs, name="hidden%d_out" % (layer + 1))
        return inputs

    def _build_graph(self, n_inputs, n_outputs):
        """Build the same model as earlier"""
        if self.random_state is not None:
            tf.set_random_seed(self.random_state)
            np.random.seed(self.random_state)

        X = tf.placeholder(tf.float32, shape=(None, n_inputs), name="X")
        y = tf.placeholder(tf.int32, shape=(None), name="y")

        if self.batch_norm_momentum or self.dropout_rate:
            self._training = tf.placeholder_with_default(False, shape=(), name='training')
        else:
            self._training = None

        dnn_outputs = self._dnn(X)

        logits = tf.layers.dense(dnn_outputs, n_outputs, kernel_initializer=he_init, name="logits")
        Y_proba = tf.nn.softmax(logits, name="Y_proba")

        xentropy = tf.nn.sparse_softmax_cross_entropy_with_logits(labels=y,
                                                                  logits=logits)
        loss = tf.reduce_mean(xentropy, name="loss")

        optimizer = self.optimizer_class(learning_rate=self.learning_rate)
        training_op = optimizer.minimize(loss)

        correct = tf.nn.in_top_k(logits, y, 1)
        accuracy = tf.reduce_mean(tf.cast(correct, tf.float32), name="accuracy")

        init = tf.global_variables_initializer()
        saver = tf.train.Saver()

        # Make the important operations available easily through instance variables
        self._X, self._y = X, y
        self._Y_proba, self._loss = Y_proba, loss
        self._training_op, self._accuracy = training_op, accuracy
        self._init, self._saver = init, saver

    def close_session(self):
        if self._session:
            self._session.close()

    def _get_model_params(self):
        """Get all variable values (used for early stopping, faster than saving to disk)"""
        with self._graph.as_default():
            gvars = tf.get_collection(tf.GraphKeys.GLOBAL_VARIABLES)
        return {gvar.op.name: value for gvar, value in zip(gvars, self._session.run(gvars))}

    def _restore_model_params(self, model_params):
        """Set all variables to the given values (for early stopping, faster than loading from disk)"""
        gvar_names = list(model_params.keys())
        assign_ops = {gvar_name: self._graph.get_operation_by_name(gvar_name + "/Assign")
                      for gvar_name in gvar_names}
        init_values = {gvar_name: assign_op.inputs[1] for gvar_name, assign_op in assign_ops.items()}
        feed_dict = {init_values[gvar_name]: model_params[gvar_name] for gvar_name in gvar_names}
        self._session.run(assign_ops, feed_dict=feed_dict)

    def fit(self, X, y, X_valid=None, y_valid=None):
        """Fit the model to the training set. If X_valid and y_valid are provided, use early stopping."""
        self.close_session()

        # infer n_inputs and n_outputs from the training set.
        n_inputs = X.shape[1]
        self.classes_ = np.unique(y)
        n_outputs = len(self.classes_)
        
        # Translate the labels vector to a vector of sorted class indices, containing
        # integers from 0 to n_outputs - 1.
        # For example, if y is equal to [8, 8, 9, 5, 7, 6, 6, 6], then the sorted class
        # labels (self.classes_) will be equal to [5, 6, 7, 8, 9], and the labels vector
        # will be translated to [3, 3, 4, 0, 2, 1, 1, 1]
        self.class_to_index_ = {label: index
                                for index, label in enumerate(self.classes_)}
        y = np.array([self.class_to_index_[label]
                      for label in y], dtype=np.int32)
        
        self._graph = tf.Graph()
        with self._graph.as_default():
            self._build_graph(n_inputs, n_outputs)
            # extra ops for batch normalization
            extra_update_ops = tf.get_collection(tf.GraphKeys.UPDATE_OPS)

        # needed in case of early stopping
        max_checks_without_progress = 20
        checks_without_progress = 0
        best_loss = np.infty
        best_params = None
        
        # Now train the model!
        self._session = tf.Session(graph=self._graph)
        with self._session.as_default() as sess:
            self._init.run()
            for epoch in range(self.n_epochs):
                start_pos=0
                for batches in range(int(len(X)/self.batch_size)):
                    X_batch,y_batch=X[start_pos:start_pos+self.batch_size],y[start_pos:start_pos+self.batch_size]
                    feed_dict = {self._X: X_batch, self._y: y_batch}
                    start_pos+=self.batch_size
                #rnd_idx = np.random.permutation(len(X))
                #for rnd_indices in np.array_split(rnd_idx, len(X) // self.batch_size):
                    #X_batch, y_batch = X[rnd_indices], y[rnd_indices]
                    #feed_dict = {self._X: X_batch, self._y: y_batch}
                    if self._training is not None:
                        feed_dict[self._training] = True
                    sess.run(self._training_op, feed_dict=feed_dict)
                    if extra_update_ops:
                        sess.run(extra_update_ops, feed_dict=feed_dict)
                if X_valid is not None and y_valid is not None:
                    loss_val, acc_val = sess.run([self._loss, self._accuracy],
                                                 feed_dict={self._X: X_valid,
                                                            self._y: y_valid})
                    if loss_val < best_loss:
                        best_params = self._get_model_params()
                        best_loss = loss_val
                        checks_without_progress = 0
                    else:
                        checks_without_progress += 1
                    print("{}\tValidation loss: {:.6f}\tBest loss: {:.6f}\tAccuracy: {:.2f}%".format(
                        epoch, loss_val, best_loss, acc_val * 100))
                    if checks_without_progress > max_checks_without_progress:
                        print("Early stopping!")
                        break
                else:
                    loss_train, acc_train = sess.run([self._loss, self._accuracy],
                                                     feed_dict={self._X: X_batch,
                                                                self._y: y_batch})
                    print("{}\tLast training batch loss: {:.6f}\tAccuracy: {:.2f}%".format(
                        epoch, loss_train, acc_train * 100))
            # If we used early stopping then rollback to the best model found
            if best_params:
                self._restore_model_params(best_params)
            return self

    def predict_proba(self, X):
        if not self._session:
            raise NotFittedError("This %s instance is not fitted yet" % self.__class__.__name__)
        with self._session.as_default() as sess:
            return self._Y_proba.eval(feed_dict={self._X: X})

    def predict(self, X):
        class_indices = np.argmax(self.predict_proba(X), axis=1)
        return np.array([[self.classes_[class_index]]
                         for class_index in class_indices], np.int32)

    def save(self, path):
        self._saver.save(self._session, path)

In [5]:
def leaky_relu(alpha=0.01):
    def parametrized_leaky_relu(z, name=None):
        return tf.maximum(alpha * z, z, name=name)
    return parametrized_leaky_relu

In [45]:
dnn_clf = DNNClassifier(random_state=42,n_neurons=10, n_hidden_layers=2,learning_rate=0.01, batch_size=100, 
                        activation=leaky_relu(alpha=0.01),dropout_rate=0.2)
dnn_clf.fit(X_train, y_train, n_epochs=100, X_valid=X_valid, y_valid=y_valid)

Instructions for updating:
Use keras.layers.dropout instead.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
0	Validation loss: 0.304389	Best loss: 0.304389	Accuracy: 90.47%
1	Validation loss: 0.292630	Best loss: 0.292630	Accuracy: 90.47%
2	Validation loss: 0.277918	Best loss: 0.277918	Accuracy: 90.47%
3	Validation loss: 0.280170	Best loss: 0.277918	Accuracy: 90.47%
4	Validation loss: 0.275851	Best loss: 0.275851	Accuracy: 90.47%
5	Validation loss: 0.275258	Best loss: 0.275258	Accuracy: 90.47%
6	Validation loss: 0.279636	Best loss: 0.275258	Accuracy: 90.47%
7	Validation loss: 0.279206	Best loss: 0.275258	Accuracy: 90.48%
8	Validation loss: 0.273765	Best loss: 0.273765	Accuracy: 90.47%
9	Validation loss: 0.276124	Best loss: 0.273765	Accuracy: 90.47%
10	Validation loss: 0.277043	Best loss: 0.273765	Accuracy: 90.47%
11	Validation loss: 0.276708	Best loss: 0.273765	Accuracy: 90.47%
12	Validation loss: 0.274710	Best loss: 0.

DNNClassifier(activation=<function leaky_relu.<locals>.parametrized_leaky_relu at 0x0000017797852D08>,
       batch_norm_momentum=None, batch_size=100, dropout_rate=0.2,
       initializer=<tensorflow.python.ops.init_ops.VarianceScaling object at 0x00000177BBFF98D0>,
       learning_rate=0.01, n_hidden_layers=2, n_neurons=10,
       optimizer_class=<class 'tensorflow.python.training.adam.AdamOptimizer'>,
       random_state=42)

In [46]:
y_pred = dnn_clf.predict_proba(X_valid)[:,1]
y_t = dnn_clf.predict_proba(X_train)[:,1]

In [47]:
print("CV score: {:<8.5f}".format(roc_auc_score(y_valid, y_pred)))
print("CV score: {:<8.5f}".format(roc_auc_score(y_train, y_t)))

CV score: 0.80927 
CV score: 0.80662 


In [28]:
from sklearn.metrics import accuracy_score
y_pred = dnn_clf.predict(X_valid)
accuracy_score(y_valid, y_pred)

0.9131

In [29]:
from sklearn.model_selection import RandomizedSearchCV

In [64]:
param_distribs = {
    "n_epochs":[150,200,50,100],
    "n_neurons": [10, 30, 50, 70, 90, 100, 120, 140, 160],
    "batch_size": [10, 50, 100, 200],
    "learning_rate": [0.01, 0.02, 0.05, 0.1],
    "activation": [leaky_relu(alpha=0.01)],
    # you could also try exploring different numbers of hidden layers, different optimizers, etc.
    "n_hidden_layers": [2,3,4,5],
    #"optimizer_class": [tf.train.AdamOptimizer, partial(tf.train.MomentumOptimizer, momentum=0.95)],
    #"dropout_rate": [0,0.1, 0.2, 0.3, 0.4, 0.5],
}

In [65]:
rnd_search = RandomizedSearchCV(DNNClassifier(random_state=42), param_distribs, n_iter=200,
                                cv=3, random_state=42, verbose=2,scoring='roc_auc')
rnd_search.fit(X_train, y_train, X_valid=X_valid, y_valid=y_valid)

Fitting 3 folds for each of 200 candidates, totalling 600 fits
[CV] n_neurons=50, n_hidden_layers=4, n_epochs=200, learning_rate=0.1, batch_size=100, activation=<function leaky_relu.<locals>.parametrized_leaky_relu at 0x0000017797852158> 
0	Validation loss: 8.891991	Best loss: 8.891991	Accuracy: 90.47%
1	Validation loss: 2.325475	Best loss: 2.325475	Accuracy: 90.47%
2	Validation loss: 0.495116	Best loss: 0.495116	Accuracy: 90.47%
3	Validation loss: 0.320089	Best loss: 0.320089	Accuracy: 90.47%
4	Validation loss: 0.408269	Best loss: 0.320089	Accuracy: 90.47%
5	Validation loss: 0.388148	Best loss: 0.320089	Accuracy: 90.47%
6	Validation loss: 0.332632	Best loss: 0.320089	Accuracy: 90.47%
7	Validation loss: 0.325866	Best loss: 0.320089	Accuracy: 90.47%
8	Validation loss: 0.356358	Best loss: 0.320089	Accuracy: 90.47%
9	Validation loss: 0.290078	Best loss: 0.290078	Accuracy: 90.47%
10	Validation loss: 0.261974	Best loss: 0.261974	Accuracy: 90.79%
11	Validation loss: 0.257579	Best loss: 0.257

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   15.3s remaining:    0.0s


0	Validation loss: 24971.400391	Best loss: 24971.400391	Accuracy: 90.47%
1	Validation loss: 551.268738	Best loss: 551.268738	Accuracy: 90.47%
2	Validation loss: 478.737061	Best loss: 478.737061	Accuracy: 90.47%
3	Validation loss: 69.219101	Best loss: 69.219101	Accuracy: 90.43%
4	Validation loss: 331.407288	Best loss: 69.219101	Accuracy: 90.47%
5	Validation loss: 118.864197	Best loss: 69.219101	Accuracy: 15.72%
6	Validation loss: 216.240845	Best loss: 69.219101	Accuracy: 90.47%
7	Validation loss: 146.275299	Best loss: 69.219101	Accuracy: 90.47%
8	Validation loss: 177.128555	Best loss: 69.219101	Accuracy: 90.47%
9	Validation loss: 4.376509	Best loss: 4.376509	Accuracy: 90.27%
10	Validation loss: 76.416229	Best loss: 4.376509	Accuracy: 90.38%
11	Validation loss: 33.237667	Best loss: 4.376509	Accuracy: 90.47%
12	Validation loss: 10.377983	Best loss: 4.376509	Accuracy: 90.31%
13	Validation loss: 10.734348	Best loss: 4.376509	Accuracy: 86.82%
14	Validation loss: 7.656748	Best loss: 4.376509	

22	Validation loss: 21.124161	Best loss: 9.828681	Accuracy: 85.55%
23	Validation loss: 39.160400	Best loss: 9.828681	Accuracy: 90.52%
24	Validation loss: 14.882450	Best loss: 9.828681	Accuracy: 77.18%
25	Validation loss: 90.187828	Best loss: 9.828681	Accuracy: 48.09%
Early stopping!
[CV]  n_neurons=90, n_hidden_layers=2, n_epochs=50, learning_rate=0.1, batch_size=10, activation=<function leaky_relu.<locals>.parametrized_leaky_relu at 0x0000017797852158>, total= 1.1min
[CV] n_neurons=90, n_hidden_layers=2, n_epochs=50, learning_rate=0.1, batch_size=10, activation=<function leaky_relu.<locals>.parametrized_leaky_relu at 0x0000017797852158> 
0	Validation loss: 38.897316	Best loss: 38.897316	Accuracy: 90.47%
1	Validation loss: 39.660194	Best loss: 38.897316	Accuracy: 90.47%
2	Validation loss: 32.081211	Best loss: 32.081211	Accuracy: 90.48%
3	Validation loss: 13.644619	Best loss: 13.644619	Accuracy: 90.75%
4	Validation loss: 9.089954	Best loss: 9.089954	Accuracy: 91.05%
5	Validation loss: 5

55	Validation loss: 0.248216	Best loss: 0.241819	Accuracy: 91.27%
56	Validation loss: 0.246123	Best loss: 0.241819	Accuracy: 91.25%
57	Validation loss: 0.244931	Best loss: 0.241819	Accuracy: 91.29%
58	Validation loss: 0.243829	Best loss: 0.241819	Accuracy: 91.26%
59	Validation loss: 0.243349	Best loss: 0.241819	Accuracy: 91.26%
60	Validation loss: 0.242529	Best loss: 0.241819	Accuracy: 91.30%
61	Validation loss: 0.242146	Best loss: 0.241819	Accuracy: 91.32%
62	Validation loss: 0.242617	Best loss: 0.241819	Accuracy: 91.26%
63	Validation loss: 0.241806	Best loss: 0.241806	Accuracy: 91.35%
64	Validation loss: 0.242259	Best loss: 0.241806	Accuracy: 91.27%
65	Validation loss: 0.241843	Best loss: 0.241806	Accuracy: 91.32%
66	Validation loss: 0.241639	Best loss: 0.241639	Accuracy: 91.30%
67	Validation loss: 0.242622	Best loss: 0.241639	Accuracy: 91.30%
68	Validation loss: 0.241570	Best loss: 0.241570	Accuracy: 91.26%
69	Validation loss: 0.241436	Best loss: 0.241436	Accuracy: 91.27%
70	Validat

...

0	Validation loss: 35.198856	Best loss: 35.198856	Accuracy: 9.53%
1	Validation loss: 27.389832	Best loss: 27.389832	Accuracy: 9.54%
2	Validation loss: 102.739059	Best loss: 27.389832	Accuracy: 9.61%
3	Validation loss: 99.619209	Best loss: 27.389832	Accuracy: 9.60%
4	Validation loss: 128.835831	Best loss: 27.389832	Accuracy: 90.47%
5	Validation loss: 134.616013	Best loss: 27.389832	Accuracy: 9.53%
6	Validation loss: 135.438187	Best loss: 27.389832	Accuracy: 9.68%
7	Validation loss: 337.355835	Best loss: 27.389832	Accuracy: 9.53%
8	Validation loss: 251.342072	Best loss: 27.389832	Accuracy: 9.58%
9	Validation loss: 219.970352	Best loss: 27.389832	Accuracy: 9.61%
10	Validation loss: 15.129457	Best loss: 15.129457	Accuracy: 90.47%
11	Validation loss: 232.058456	Best loss: 15.129457	Accuracy: 9.53%
12	Validation loss: 295.871704	Best loss: 15.129457	Accuracy: 10.39%
13	Validation loss: 284.317657	Best loss: 15.129457	Accuracy: 9.53%
14	Validation loss: 229.284897	Best loss: 15.129457	Accurac

[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed: 360.1min finished


0	Validation loss: 0.264035	Best loss: 0.264035	Accuracy: 90.54%
1	Validation loss: 0.254445	Best loss: 0.254445	Accuracy: 90.85%
2	Validation loss: 0.247714	Best loss: 0.247714	Accuracy: 91.18%
3	Validation loss: 0.247076	Best loss: 0.247076	Accuracy: 91.21%
4	Validation loss: 0.244753	Best loss: 0.244753	Accuracy: 91.31%
5	Validation loss: 0.244806	Best loss: 0.244753	Accuracy: 91.20%
6	Validation loss: 0.244368	Best loss: 0.244368	Accuracy: 91.18%
7	Validation loss: 0.248657	Best loss: 0.244368	Accuracy: 91.31%
8	Validation loss: 0.244690	Best loss: 0.244368	Accuracy: 91.20%
9	Validation loss: 0.243566	Best loss: 0.243566	Accuracy: 91.18%
10	Validation loss: 0.243788	Best loss: 0.243566	Accuracy: 91.17%
11	Validation loss: 0.243546	Best loss: 0.243546	Accuracy: 91.25%
12	Validation loss: 0.243440	Best loss: 0.243440	Accuracy: 91.29%
13	Validation loss: 0.245108	Best loss: 0.243440	Accuracy: 91.25%
14	Validation loss: 0.256734	Best loss: 0.243440	Accuracy: 91.14%
15	Validation loss: 

124	Validation loss: 0.236955	Best loss: 0.235828	Accuracy: 91.35%
125	Validation loss: 0.238327	Best loss: 0.235828	Accuracy: 91.36%
126	Validation loss: 0.236899	Best loss: 0.235828	Accuracy: 91.31%
127	Validation loss: 0.235834	Best loss: 0.235828	Accuracy: 91.37%
128	Validation loss: 0.235944	Best loss: 0.235828	Accuracy: 91.40%
129	Validation loss: 0.236120	Best loss: 0.235828	Accuracy: 91.32%
130	Validation loss: 0.235990	Best loss: 0.235828	Accuracy: 91.35%
131	Validation loss: 0.235822	Best loss: 0.235822	Accuracy: 91.44%
132	Validation loss: 0.235973	Best loss: 0.235822	Accuracy: 91.37%
133	Validation loss: 0.235876	Best loss: 0.235822	Accuracy: 91.38%
134	Validation loss: 0.236487	Best loss: 0.235822	Accuracy: 91.34%
135	Validation loss: 0.235561	Best loss: 0.235561	Accuracy: 91.38%
136	Validation loss: 0.236173	Best loss: 0.235561	Accuracy: 91.35%
137	Validation loss: 0.236515	Best loss: 0.235561	Accuracy: 91.37%
138	Validation loss: 0.235899	Best loss: 0.235561	Accuracy: 91

RandomizedSearchCV(cv=3, error_score='raise',
          estimator=DNNClassifier(activation=<function elu at 0x00000177B7FEE598>,
       batch_norm_momentum=None, batch_size=20, dropout_rate=None,
       initializer=<tensorflow.python.ops.init_ops.VarianceScaling object at 0x00000177BBFF98D0>,
       learning_rate=0.01, n_epochs=100, n_hidden_layers=5, n_neurons=100,
       optimizer_class=<class 'tensorflow.python.training.adam.AdamOptimizer'>,
       random_state=42),
          fit_params=None, iid=True, n_iter=200, n_jobs=1,
          param_distributions={'n_epochs': [150, 200, 50, 100], 'n_neurons': [10, 30, 50, 70, 90, 100, 120, 140, 160], 'batch_size': [10, 50, 100, 200], 'learning_rate': [0.01, 0.02, 0.05, 0.1], 'activation': [<function leaky_relu.<locals>.parametrized_leaky_relu at 0x0000017797852158>], 'n_hidden_layers': [2, 3, 4, 5]},
          pre_dispatch='2*n_jobs', random_state=42, refit=True,
          return_train_score='warn', scoring='roc_auc', verbose=2)

In [66]:
rnd_search.best_params_, rnd_search.best_score_

({'n_neurons': 50,
  'n_hidden_layers': 2,
  'n_epochs': 200,
  'learning_rate': 0.01,
  'batch_size': 100,
  'activation': <function __main__.leaky_relu.<locals>.parametrized_leaky_relu(z, name=None)>},
 0.8360516031155636)

In [4]:
from hyperopt import fmin, tpe, hp, STATUS_OK, Trials
from sklearn.model_selection import cross_val_score

In [13]:
best = 0

def hyperopt_train_test(params):
    clf = DNNClassifier(**params)
    return cross_val_score(clf, X_small, y_small,scoring='roc_auc', cv=3, n_jobs=1).mean()

def loss(params):
    global best
    roc = hyperopt_train_test(params)
    if roc > best:
        best = roc
        print ('new best:', best, params)
    return {'loss': -roc, 'status': STATUS_OK}

trials = Trials()

In [16]:
space4nn = {
    'n_epochs': hp.choice('n_epochs', np.arange(10,1000, 10)),
    'n_neurons': hp.choice('n_neurons', np.arange(2,200,2)),
    'batch_size': hp.choice('batch_size', np.arange(50,1000,50)),
    'learning_rate': hp.uniform('learning_rate', 0.01, 0.2),
    'activation': hp.choice('activation',[leaky_relu(alpha=0.01)]),
    'n_hidden_layers': hp.choice('n_hidden_layers', [1,2,3,4,5,6,7,8,9,10]),
    'dropout_rate': hp.uniform('dropout_rate', 0, 0.5)
}

In [ ]:
best_cv = fmin(loss, space4nn, algo=tpe.suggest, max_evals=50, trials=trials)

0	Last training batch loss: 0.447060	Accuracy: 88.57%                                                                  
1	Last training batch loss: 6.567778	Accuracy: 88.57%                                                                  
2	Last training batch loss: 1.975139	Accuracy: 71.14%                                                                  
3	Last training batch loss: 0.969345	Accuracy: 84.00%                                                                  
4	Last training batch loss: 6.510269	Accuracy: 88.57%                                                                  
5	Last training batch loss: 1.772741	Accuracy: 88.57%                                                                  
6	Last training batch loss: 2.548368	Accuracy: 88.57%                                                                  
7	Last training batch loss: 3.378826	Accuracy: 88.57%                                                                  
8	Last training batch loss: 1.049014	Acc

136	Last training batch loss: 2.705355	Accuracy: 89.14%                                                                
137	Last training batch loss: 1.539694	Accuracy: 89.14%                                                                
138	Last training batch loss: 15.378869	Accuracy: 88.57%                                                               
139	Last training batch loss: 1.609080	Accuracy: 88.86%                                                                
140	Last training batch loss: 2.305024	Accuracy: 88.57%                                                                
141	Last training batch loss: 6.645732	Accuracy: 88.57%                                                                
142	Last training batch loss: 0.976295	Accuracy: 87.14%                                                                
143	Last training batch loss: 6.087749	Accuracy: 88.57%                                                                
144	Last training batch loss: 20.195963	

272	Last training batch loss: 34.077839	Accuracy: 88.57%                                                               
273	Last training batch loss: 3.788712	Accuracy: 88.29%                                                                
274	Last training batch loss: 3.510803	Accuracy: 88.86%                                                                
275	Last training batch loss: 12.826350	Accuracy: 88.57%                                                               
276	Last training batch loss: 24.465664	Accuracy: 88.57%                                                               
277	Last training batch loss: 7.448510	Accuracy: 88.57%                                                                
278	Last training batch loss: 16.622272	Accuracy: 88.57%                                                               
279	Last training batch loss: 1.566222	Accuracy: 84.00%                                                                
280	Last training batch loss: 11.931349	

408	Last training batch loss: 3.383006	Accuracy: 62.29%                                                                
409	Last training batch loss: 1.896524	Accuracy: 89.14%                                                                
410	Last training batch loss: 7.669405	Accuracy: 88.57%                                                                
411	Last training batch loss: 1.159982	Accuracy: 88.86%                                                                
412	Last training batch loss: 8.452534	Accuracy: 88.57%                                                                
413	Last training batch loss: 8.345720	Accuracy: 88.57%                                                                
414	Last training batch loss: 27.868229	Accuracy: 88.57%                                                               
415	Last training batch loss: 1.593166	Accuracy: 76.00%                                                                
416	Last training batch loss: 1.223162	A

544	Last training batch loss: 10.422090	Accuracy: 88.57%                                                               
545	Last training batch loss: 44.644897	Accuracy: 88.57%                                                               
546	Last training batch loss: 21.144272	Accuracy: 88.57%                                                               
547	Last training batch loss: 2.448012	Accuracy: 88.86%                                                                
548	Last training batch loss: 2.007145	Accuracy: 87.14%                                                                
549	Last training batch loss: 15.451573	Accuracy: 88.57%                                                               
550	Last training batch loss: 1.602410	Accuracy: 88.57%                                                                
551	Last training batch loss: 9.823763	Accuracy: 24.29%                                                                
552	Last training batch loss: 3.309999	A

...

50	Last training batch loss: nan	Accuracy: 0.00%                                                                       
51	Last training batch loss: nan	Accuracy: 0.00%                                                                       
52	Last training batch loss: nan	Accuracy: 0.00%                                                                       
53	Last training batch loss: nan	Accuracy: 0.00%                                                                       
54	Last training batch loss: nan	Accuracy: 0.00%                                                                       
55	Last training batch loss: nan	Accuracy: 0.00%                                                                       
56	Last training batch loss: nan	Accuracy: 0.00%                                                                       
57	Last training batch loss: nan	Accuracy: 0.00%                                                                       
58	Last training batch loss: nan	Accurac

186	Last training batch loss: nan	Accuracy: 0.00%                                                                      
187	Last training batch loss: nan	Accuracy: 0.00%                                                                      
188	Last training batch loss: nan	Accuracy: 0.00%                                                                      
189	Last training batch loss: nan	Accuracy: 0.00%                                                                      
190	Last training batch loss: nan	Accuracy: 0.00%                                                                      
191	Last training batch loss: nan	Accuracy: 0.00%                                                                      
192	Last training batch loss: nan	Accuracy: 0.00%                                                                      
193	Last training batch loss: nan	Accuracy: 0.00%                                                                      
194	Last training batch loss: nan	Accura

322	Last training batch loss: nan	Accuracy: 0.00%                                                                      
323	Last training batch loss: nan	Accuracy: 0.00%                                                                      
324	Last training batch loss: nan	Accuracy: 0.00%                                                                      
325	Last training batch loss: nan	Accuracy: 0.00%                                                                      
326	Last training batch loss: nan	Accuracy: 0.00%                                                                      
327	Last training batch loss: nan	Accuracy: 0.00%                                                                      
328	Last training batch loss: nan	Accuracy: 0.00%                                                                      
329	Last training batch loss: nan	Accuracy: 0.00%                                                                      
330	Last training batch loss: nan	Accura

458	Last training batch loss: nan	Accuracy: 0.00%                                                                      
459	Last training batch loss: nan	Accuracy: 0.00%                                                                      
460	Last training batch loss: nan	Accuracy: 0.00%                                                                      
461	Last training batch loss: nan	Accuracy: 0.00%                                                                      
462	Last training batch loss: nan	Accuracy: 0.00%                                                                      
463	Last training batch loss: nan	Accuracy: 0.00%                                                                      
464	Last training batch loss: nan	Accuracy: 0.00%                                                                      
465	Last training batch loss: nan	Accuracy: 0.00%                                                                      
466	Last training batch loss: nan	Accura

594	Last training batch loss: nan	Accuracy: 0.00%                                                                      
595	Last training batch loss: nan	Accuracy: 0.00%                                                                      
596	Last training batch loss: nan	Accuracy: 0.00%                                                                      
597	Last training batch loss: nan	Accuracy: 0.00%                                                                      
598	Last training batch loss: nan	Accuracy: 0.00%                                                                      
599	Last training batch loss: nan	Accuracy: 0.00%                                                                      
600	Last training batch loss: nan	Accuracy: 0.00%                                                                      
601	Last training batch loss: nan	Accuracy: 0.00%                                                                      
602	Last training batch loss: nan	Accura

## A simple NN
from https://www.kaggle.com/jotel1/nn-input-shape-why-it-matters

In [4]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import KFold, StratifiedKFold
from sklearn.metrics import roc_auc_score
import tensorflow as tf

In [6]:
from tensorflow import keras
from tensorflow.python.keras.models import Sequential, Model
from tensorflow.python.keras.layers import Dense, Input, Flatten, Dropout, BatchNormalization, GaussianNoise
from tensorflow.python.keras import callbacks
import tensorflow.python.keras.backend as K

In [7]:
train = pd.read_csv('data/train.csv', index_col=0)
y_train = train.pop('target')
len_train = len(train)
test = pd.read_csv('data/test.csv', index_col=0)
df_all = pd.concat((train, test), sort=False)
prev_cols = df_all.columns

In [19]:
# PREPROCESS
scaler = StandardScaler()
df_all[prev_cols] = scaler.fit_transform(df_all[prev_cols])
train = df_all[0:len_train]
test = df_all[len_train:]

In [17]:
train.head()

var_0     var_1     var_2     var_3     var_4     var_5     var_6  \
ID_code                                                                         
train_0 -0.573930 -1.275655  0.453774 -0.829761  0.236655 -0.537163 -0.338885   
train_1  0.273590 -0.623288  1.193406 -0.685231  0.793204  1.538372  0.241141   
train_2 -0.677998 -0.276809  0.519141  0.537312 -0.305510 -0.511776  1.768200   
train_3  0.128711 -0.129996 -0.666993  0.196935  0.930505  0.409577  0.497595   
train_4 -0.273969  0.035234  0.820234 -0.075620  0.740728  0.954270  0.610458   

            var_7     var_8     var_9    ...      var_190   var_191   var_192  \
ID_code                                  ...                                    
train_0  0.610620 -1.560352 -1.476589    ...     0.268524 -1.152071  0.817682   
train_1 -0.001080  0.859932  0.418964    ...     0.972423  0.090291  0.444032   
train_2 -0.561777 -1.560142 -1.309985    ...    -0.067258  0.774463 -0.173400   
train_3 -0.471313 -1.842650  0.548599    ...     0.275373 -0.894453 -0.817400   
train_4  0.793242  1.795606  0.089243    ...    -1.032263  0.685482 -1.404613   

          var_193   var_194   var_195   var_196   var_197   var_198   var_199  
ID_code                                                                        
train_0 -0.409608  0.168050 -1.580891  1.024023 -0.376431 -1.026522  0.210689  
train_1  1.909132 -0.817386  1.519224  1.069580 -0.131768  0.825978  0.502789  
train_2 -0.410910  1.150076  2.294165 -1.617955 -0.697728 -0.381335  0.353504  
train_3 -0.477112  1.605954 -0.792379 -0.958584  1.500010  0.697631 -0.548374  
train_4  1.469101 -1.500294 -0.961315  0.298987  0.643471  0.706835 -0.530213  

[5 rows x 200 columns]

In [14]:
# CROSS VALIDATION
cv = StratifiedKFold(n_splits=10, shuffle=True, random_state=1111)

In [28]:
# LOGGER
class Logger(callbacks.Callback):
    def __init__(self, out_path='./', patience=10, lr_patience=3, out_fn='', log_fn='', validation_data=()):
        self.auc = 0
        self.path = out_path
        self.fn = out_fn
        self.patience = patience
        self.lr_patience = lr_patience
        self.no_improve = 0
        self.no_improve_lr = 0
        self.validation_data=validation_data
        
    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):
        cv_pred = self.model.predict(self.validation_data[0], batch_size=1024)
        cv_true = self.validation_data[1]
        auc_val = roc_auc_score(cv_true, cv_pred)
        if self.auc < auc_val:
            self.no_improve = 0
            self.no_improve_lr = 0
            print("Epoch %s - best AUC: %s" % (epoch, round(auc_val, 4)))
            self.auc = auc_val
            self.model.save(self.path + self.fn, overwrite=True)
        else:
            self.no_improve += 1
            self.no_improve_lr += 1
            print("Epoch %s - current AUC: %s" % (epoch, round(auc_val, 4)))
            if self.no_improve >= self.patience:
                self.model.stop_training = True
            if self.no_improve_lr >= self.lr_patience:
                lr = float(K.get_value(self.model.optimizer.lr))
                K.set_value(self.model.optimizer.lr, 0.75*lr)
                print("Setting lr to {}".format(0.75*lr))
                self.no_improve_lr = 0

        return

In [11]:
# MODEL DEF
def _Model():
    inp = Input(shape=(200, 1))
    d1 = Dense(16, activation='relu')(inp)
    fl = Flatten()(d1)
    preds = Dense(1, activation='sigmoid')(fl)
    model = Model(inputs=inp, outputs=preds)
    model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
    return model

In [32]:
preds = []
c = 0
oof_preds = np.zeros((200000, 1))
for train_idx, valid_idx in cv.split(train, y_train):
    print("VAL %s" % c)
    X_train = np.reshape(train.iloc[train_idx].values, (-1, 200, 1))
    y_train_ = y_train.iloc[train_idx].values
    X_valid = np.reshape(train.iloc[valid_idx].values, (-1, 200, 1))
    y_valid = y_train.iloc[valid_idx].values
    model = _Model()
    logger = Logger(patience=10, out_path='./', out_fn='cv_{}.h5'.format(c), validation_data=(X_valid, y_valid))
    model.fit(X_train, y_train_, validation_data=(X_valid, y_valid), epochs=100, verbose=2, batch_size=256,
              callbacks=[logger])
    model.load_weights('cv_{}.h5'.format(c))
    X_test = np.reshape(test.values, (200000, 200, 1))
    curr_preds = model.predict(X_test, batch_size=2048)
    oof_preds[valid_idx] = model.predict(X_valid)
    preds.append(curr_preds)
    c += 1
auc = roc_auc_score(y_train, oof_preds)
print("CV_AUC: {}".format(auc))

# SAVE DATA
preds = np.asarray(preds)
preds = preds.reshape((5, 200000))
preds_final = np.mean(preds.T, axis=1)

VAL 0
Train on 179999 samples, validate on 20001 samples
Epoch 1/100
Epoch 0 - best AUC: 0.864
 - 7s - loss: 0.2555 - acc: 0.9081 - val_loss: 0.2305 - val_acc: 0.9131
Epoch 2/100
Epoch 1 - best AUC: 0.8787
 - 6s - loss: 0.2252 - acc: 0.9165 - val_loss: 0.2201 - val_acc: 0.9175
Epoch 3/100
Epoch 2 - best AUC: 0.8851
 - 6s - loss: 0.2154 - acc: 0.9199 - val_loss: 0.2146 - val_acc: 0.9198
Epoch 4/100
Epoch 3 - best AUC: 0.887
 - 6s - loss: 0.2121 - acc: 0.9206 - val_loss: 0.2128 - val_acc: 0.9200
Epoch 5/100
Epoch 4 - best AUC: 0.8888
 - 6s - loss: 0.2100 - acc: 0.9215 - val_loss: 0.2110 - val_acc: 0.9221
Epoch 6/100
Epoch 5 - best AUC: 0.8903
 - 6s - loss: 0.2084 - acc: 0.9223 - val_loss: 0.2100 - val_acc: 0.9218
Epoch 7/100
Epoch 6 - best AUC: 0.8911
 - 6s - loss: 0.2068 - acc: 0.9228 - val_loss: 0.2093 - val_acc: 0.9220
Epoch 8/100
Epoch 7 - best AUC: 0.8923
 - 6s - loss: 0.2059 - acc: 0.9231 - val_loss: 0.2081 - val_acc: 0.9224
Epoch 9/100
Epoch 8 - current AUC: 0.8923
 - 6s - loss: 0

Epoch 39/100
Epoch 38 - current AUC: 0.8938
 - 6s - loss: 0.1982 - acc: 0.9261 - val_loss: 0.2070 - val_acc: 0.9219
Epoch 40/100
Epoch 39 - current AUC: 0.8937
 - 6s - loss: 0.1985 - acc: 0.9260 - val_loss: 0.2070 - val_acc: 0.9218
Epoch 41/100
Epoch 40 - current AUC: 0.8937
Setting lr to 0.0004218749818392098
 - 6s - loss: 0.1983 - acc: 0.9259 - val_loss: 0.2075 - val_acc: 0.9215
Epoch 42/100
Epoch 41 - best AUC: 0.8938
 - 6s - loss: 0.1977 - acc: 0.9261 - val_loss: 0.2069 - val_acc: 0.9215
Epoch 43/100
Epoch 42 - best AUC: 0.8938
 - 6s - loss: 0.1977 - acc: 0.9265 - val_loss: 0.2071 - val_acc: 0.9216
Epoch 44/100
Epoch 43 - current AUC: 0.8938
 - 6s - loss: 0.1976 - acc: 0.9262 - val_loss: 0.2067 - val_acc: 0.9216
Epoch 45/100
Epoch 44 - best AUC: 0.8939
 - 6s - loss: 0.1976 - acc: 0.9261 - val_loss: 0.2068 - val_acc: 0.9216
Epoch 46/100
Epoch 45 - current AUC: 0.8938
 - 6s - loss: 0.1977 - acc: 0.9261 - val_loss: 0.2083 - val_acc: 0.9221
Epoch 47/100
Epoch 46 - current AUC: 0.8937
 

Epoch 17/100
Epoch 16 - best AUC: 0.8944
 - 6s - loss: 0.2007 - acc: 0.9250 - val_loss: 0.2064 - val_acc: 0.9231
Epoch 18/100
Epoch 17 - best AUC: 0.8944
 - 6s - loss: 0.2009 - acc: 0.9247 - val_loss: 0.2066 - val_acc: 0.9231
Epoch 19/100
Epoch 18 - current AUC: 0.8942
 - 6s - loss: 0.2007 - acc: 0.9247 - val_loss: 0.2065 - val_acc: 0.9236
Epoch 20/100
Epoch 19 - current AUC: 0.8941
 - 6s - loss: 0.2005 - acc: 0.9246 - val_loss: 0.2084 - val_acc: 0.9233
Epoch 21/100
Epoch 20 - current AUC: 0.8941
Setting lr to 0.0007500000356230885
 - 6s - loss: 0.2004 - acc: 0.9245 - val_loss: 0.2075 - val_acc: 0.9241
Epoch 22/100
Epoch 21 - best AUC: 0.8948
 - 6s - loss: 0.1995 - acc: 0.9254 - val_loss: 0.2061 - val_acc: 0.9241
Epoch 23/100
Epoch 22 - current AUC: 0.8945
 - 6s - loss: 0.1997 - acc: 0.9253 - val_loss: 0.2064 - val_acc: 0.9241
Epoch 24/100
Epoch 23 - current AUC: 0.8944
 - 6s - loss: 0.1994 - acc: 0.9252 - val_loss: 0.2068 - val_acc: 0.9237
Epoch 25/100
Epoch 24 - current AUC: 0.8947
S

Epoch 9/100
Epoch 8 - best AUC: 0.8994
 - 6s - loss: 0.2046 - acc: 0.9236 - val_loss: 0.2036 - val_acc: 0.9237
Epoch 10/100
Epoch 9 - best AUC: 0.8999
 - 6s - loss: 0.2040 - acc: 0.9240 - val_loss: 0.2018 - val_acc: 0.9257
Epoch 11/100
Epoch 10 - best AUC: 0.9005
 - 6s - loss: 0.2034 - acc: 0.9241 - val_loss: 0.2065 - val_acc: 0.9234
Epoch 12/100
Epoch 11 - best AUC: 0.9011
 - 6s - loss: 0.2030 - acc: 0.9238 - val_loss: 0.2010 - val_acc: 0.9252
Epoch 13/100
Epoch 12 - best AUC: 0.9016
 - 6s - loss: 0.2027 - acc: 0.9243 - val_loss: 0.2006 - val_acc: 0.9257
Epoch 14/100
Epoch 13 - best AUC: 0.9021
 - 6s - loss: 0.2020 - acc: 0.9244 - val_loss: 0.2023 - val_acc: 0.9252
Epoch 15/100
Epoch 14 - best AUC: 0.9021
 - 6s - loss: 0.2017 - acc: 0.9245 - val_loss: 0.2000 - val_acc: 0.9259
Epoch 16/100
Epoch 15 - best AUC: 0.9025
 - 6s - loss: 0.2020 - acc: 0.9244 - val_loss: 0.1999 - val_acc: 0.9263
Epoch 17/100
Epoch 16 - current AUC: 0.9023
 - 6s - loss: 0.2018 - acc: 0.9248 - val_loss: 0.2029 -

Epoch 32/100
Epoch 31 - current AUC: 0.8966
Setting lr to 0.0005625000048894435
 - 6s - loss: 0.1989 - acc: 0.9258 - val_loss: 0.2061 - val_acc: 0.9219
Epoch 33/100
Epoch 32 - current AUC: 0.8968
 - 6s - loss: 0.1985 - acc: 0.9257 - val_loss: 0.2060 - val_acc: 0.9211
Epoch 34/100
Epoch 33 - current AUC: 0.8968
 - 6s - loss: 0.1982 - acc: 0.9258 - val_loss: 0.2062 - val_acc: 0.9206
Epoch 35/100
Epoch 34 - current AUC: 0.8966
Setting lr to 0.0004218749818392098
 - 6s - loss: 0.1983 - acc: 0.9258 - val_loss: 0.2059 - val_acc: 0.9211
Epoch 36/100
Epoch 35 - current AUC: 0.8968
 - 6s - loss: 0.1979 - acc: 0.9262 - val_loss: 0.2059 - val_acc: 0.9213
Epoch 37/100
Epoch 36 - current AUC: 0.8968
 - 6s - loss: 0.1979 - acc: 0.9257 - val_loss: 0.2058 - val_acc: 0.9214
Epoch 38/100
Epoch 37 - current AUC: 0.8968
Setting lr to 0.00031640623637940735
 - 6s - loss: 0.1978 - acc: 0.9259 - val_loss: 0.2064 - val_acc: 0.9204
Epoch 39/100
Epoch 38 - current AUC: 0.8967
 - 6s - loss: 0.1976 - acc: 0.9259 

Epoch 5/100
Epoch 4 - best AUC: 0.8908
 - 6s - loss: 0.2101 - acc: 0.9215 - val_loss: 0.2093 - val_acc: 0.9215
Epoch 6/100
Epoch 5 - best AUC: 0.8921
 - 6s - loss: 0.2085 - acc: 0.9219 - val_loss: 0.2083 - val_acc: 0.9215
Epoch 7/100
Epoch 6 - best AUC: 0.8932
 - 6s - loss: 0.2073 - acc: 0.9227 - val_loss: 0.2071 - val_acc: 0.9219
Epoch 8/100
Epoch 7 - best AUC: 0.8941
 - 6s - loss: 0.2056 - acc: 0.9233 - val_loss: 0.2062 - val_acc: 0.9223
Epoch 9/100
Epoch 8 - best AUC: 0.8951
 - 6s - loss: 0.2053 - acc: 0.9237 - val_loss: 0.2071 - val_acc: 0.9237
Epoch 10/100
Epoch 9 - best AUC: 0.8957
 - 6s - loss: 0.2042 - acc: 0.9240 - val_loss: 0.2049 - val_acc: 0.9238
Epoch 11/100
Epoch 10 - best AUC: 0.8963
 - 6s - loss: 0.2034 - acc: 0.9240 - val_loss: 0.2049 - val_acc: 0.9235
Epoch 12/100
Epoch 11 - best AUC: 0.8966
 - 6s - loss: 0.2029 - acc: 0.9244 - val_loss: 0.2080 - val_acc: 0.9226
Epoch 13/100
Epoch 12 - best AUC: 0.8967
 - 6s - loss: 0.2023 - acc: 0.9245 - val_loss: 0.2041 - val_acc: 0

Epoch 35/100
Epoch 34 - current AUC: 0.9049
 - 6s - loss: 0.1989 - acc: 0.9253 - val_loss: 0.1962 - val_acc: 0.9266
Epoch 36/100
Epoch 35 - current AUC: 0.905
Setting lr to 0.00031640623637940735
 - 6s - loss: 0.1989 - acc: 0.9255 - val_loss: 0.1962 - val_acc: 0.9266
Epoch 37/100
Epoch 36 - best AUC: 0.9051
 - 6s - loss: 0.1986 - acc: 0.9258 - val_loss: 0.1962 - val_acc: 0.9262
Epoch 38/100
Epoch 37 - best AUC: 0.9051
 - 6s - loss: 0.1986 - acc: 0.9256 - val_loss: 0.1966 - val_acc: 0.9261
Epoch 39/100
Epoch 38 - current AUC: 0.9051
 - 6s - loss: 0.1986 - acc: 0.9258 - val_loss: 0.1961 - val_acc: 0.9267
Epoch 40/100
Epoch 39 - current AUC: 0.9051
 - 6s - loss: 0.1986 - acc: 0.9257 - val_loss: 0.1962 - val_acc: 0.9263
Epoch 41/100
Epoch 40 - best AUC: 0.9052
 - 6s - loss: 0.1985 - acc: 0.9257 - val_loss: 0.1965 - val_acc: 0.9266
Epoch 42/100
Epoch 41 - current AUC: 0.9051
 - 6s - loss: 0.1985 - acc: 0.9256 - val_loss: 0.1961 - val_acc: 0.9266
Epoch 43/100
Epoch 42 - current AUC: 0.9051
 

Epoch 42/100
Epoch 41 - current AUC: 0.8997
 - 6s - loss: 0.1985 - acc: 0.9257 - val_loss: 0.2014 - val_acc: 0.9249
Epoch 43/100
Epoch 42 - current AUC: 0.8998
Setting lr to 0.00031640623637940735
 - 6s - loss: 0.1985 - acc: 0.9256 - val_loss: 0.2045 - val_acc: 0.9237
Epoch 44/100
Epoch 43 - current AUC: 0.8999
 - 6s - loss: 0.1981 - acc: 0.9258 - val_loss: 0.2003 - val_acc: 0.9244
Epoch 45/100
Epoch 44 - current AUC: 0.8998
 - 6s - loss: 0.1980 - acc: 0.9258 - val_loss: 0.2004 - val_acc: 0.9245
Epoch 46/100
Epoch 45 - current AUC: 0.8999
Setting lr to 0.00023730468819849193
 - 6s - loss: 0.1979 - acc: 0.9258 - val_loss: 0.2003 - val_acc: 0.9247
Epoch 47/100
Epoch 46 - current AUC: 0.8999
 - 6s - loss: 0.1977 - acc: 0.9260 - val_loss: 0.2003 - val_acc: 0.9245
CV_AUC: 0.8980200229512291


ValueError: cannot reshape array of size 2000000 into shape (5,200000)

In [34]:
preds = preds.reshape((10, 200000))

In [35]:
preds_final = np.mean(preds.T, axis=1)

In [37]:
np.mean(preds_final), np.mean(oof_preds)

(0.089384645, 0.09759519620270177)

In [38]:
blend_train=pd.read_csv('data/oof_train.csv')
blend_train['nn']=oof_preds

In [39]:
blend_train.describe()

lgb            xgb             et             rf  \
count  200000.000000  200000.000000  200000.000000  200000.000000   
mean        0.122426       0.031736       0.141378       0.462142   
std         0.184817       0.095804       0.014480       0.029265   
min         0.000081       0.000011       0.093032       0.362467   
25%         0.016470       0.001674       0.131309       0.441959   
50%         0.046171       0.004947       0.140074       0.460285   
75%         0.135814       0.016842       0.149925       0.480155   
max         0.999214       0.998312       0.235257       0.601022   

                  nb        knn1024        knn2048        knn4096  \
count  200000.000000  200000.000000  200000.000000  200000.000000   
mean        0.532505       0.035991       0.038355       0.041225   
std         6.822721       0.012571       0.011733       0.011122   
min         0.000252       0.003906       0.006836       0.011719   
25%         0.020133       0.027344       0.030273       0.033447   
50%         0.054885       0.034180       0.036621       0.039795   
75%         0.170041       0.042969       0.044434       0.047363   
max      1309.814299       0.145508       0.145508       0.132080   

             knn6000             nn  
count  200000.000000  200000.000000  
mean        0.117915       0.097595  
std         0.026835       0.179971  
min         0.041833       0.000041  
25%         0.099000       0.007760  
50%         0.114667       0.024959  
75%         0.133000       0.088483  
max         0.310500       0.999800

In [40]:
blend_train.to_csv('data/oof_train.csv', index=False)

In [43]:
#blend_test=pd.read_csv("data/test_pred_layer_1.csv")
blend_test.head()

lgb       xgb        et        rf        nb   knn1024        nn
0  0.134720  0.022655  0.154304  0.491752  0.204608  0.214844  0.110927
1  0.264784  0.051081  0.160143  0.494850  0.236639  0.214844  0.138792
2  0.218526  0.042573  0.153379  0.492851  0.240824  0.177734  0.186506
3  0.285479  0.052082  0.151167  0.486449  0.274298  0.252930  0.119896
4  0.054618  0.008402  0.139684  0.460632  0.080601  0.184570  0.020572

In [42]:
blend_test['nn']=preds_final

In [44]:
blend_test.to_csv("data/test_pred_layer_1.csv", index=False)